In [23]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
from scipy.signal import medfilt2d, medfilt

In [39]:
## Change Variables here
file_name = 'unseen' #'test' #'unseen'
# Plot from this gait number
# test max gait 303
# unseen max gait 302
select = 124 
num_gait = 5 # Number of gaits to plot in one diagram

In [33]:
discard_col = ['Unnamed: 0','rightexternaloblique']
imu_train = pd.read_csv(f'imu_{file_name}.csv').drop('Unnamed: 0', axis=1)
emg_train = pd.read_csv(f'emg_{file_name}_actual.csv').drop(discard_col, axis=1)

In [34]:
all_times = np.array(imu_train['Time']).reshape(-1,101)

In [35]:
FNN = np.array(pd.read_csv(f'FNN_{file_name}.csv').drop('Unnamed: 0', axis=1))
LSTM = np.array(pd.read_csv(f'LSTM_{file_name}.csv').drop('Unnamed: 0', axis=1))

In [36]:
FNN = FNN.reshape(-1,101,FNN.shape[1])
LSTM = LSTM.reshape(-1,101,LSTM.shape[1])
test_out = emg_train.values.reshape(-1, 101, emg_train.shape[1])

In [37]:
for j in range(test_out.shape[2]):
  test_out[:,:,j] =  medfilt2d(test_out[:,:,j],5)
  FNN[:,:,j] =  medfilt2d(FNN[:,:,j],5)
  LSTM[:,:,j] =  medfilt2d(LSTM[:,:,j],5)

In [30]:
columns = ['Gastrocnemius', 'Tibialis Anterior', 'Soleus', 'Vastus Medialis', 'Vastus Lateralis', 'Rectus Femoris', 'Biceps Femoris', 'Semitendinosus', 'Gracilis', 'Gluteus Medius']

if num_gait == 1:
  x= np.linspace(0,100, num=101)
else:
  # x = all_times[sel_gait]
  x = all_times[select:select+num_gait]
  for a in range(x.shape[0]):
    x[a,:] = x[a,:]-x[a,0]
    if a >0:
      x[a,:] = x[a,:] + x[a-1,-1]

x = x.reshape(-1)
fig_plt = plt.figure(figsize = (40,40), facecolor='white')
fig_plt.set_dpi(300.0)
# set the spacing between subplots
fig_plt.subplots_adjust(left=0.1,
                    bottom=0.1,
                    right=0.9,
                    top=0.9,
                    wspace=0.1,
                    hspace=0.4)

for i in range(FNN[select:select+num_gait].shape[2]):
  if i == 8:
    continue
  if i == 9:
    plt.subplot(5, 2, i)
  else:
    plt.subplot(5, 2, i+1)
  a = FNN[select:select+num_gait].reshape([-1,FNN.shape[2]])
  b = LSTM[select:select+num_gait].reshape([-1,LSTM.shape[2]])
  c = test_out[select:select+num_gait].reshape([-1,test_out.shape[2]])

  plt.plot(x, a[:,i], color='green', label='FNN', linestyle='dotted', linewidth=4)
  plt.plot(x, c[:,i], color='red', label='Actual', linestyle='solid')
  plt.plot(x, b[:,i], color='blue', label='LSTM', linestyle=(5, (10, 3)))
  plt.title(columns[i], color = 'black', fontsize = 30)
  if num_gait == 1:
    plt.xlabel('Gait (%)')
  else:
    plt.axvline(x=x[0], color='black', linestyle=(0, (1, 8)), label="Gait Cycle")
    for j in range(num_gait+1):
      plt.axvline(x=x[j*101-1], color='black', linestyle=(0, (1, 8)))
    plt.xlabel('Time (s)', fontsize = 24)
  plt.ylabel('Normalized EMG', fontsize = 24)
  plt.yticks(fontsize=20)
  plt.xticks(fontsize=20)
  plt.legend(bbox_to_anchor=(0, 1, 1, 0), loc="lower left", ncol=2, fontsize=22)